# Time Frequency Analysis
## Moving window analysis
One way to analyse the time-varying frequency content of a signal is to
apply windows in the time domain to the signal and to calculate a Fourier spectrum
of the windowed part. The window marches along the signal with defined overlap creating
a series of Fourier spectra associated with the center times of the windows. The resulting amplitude
spectra are the plotted versus window center time. In more detail:

1. Choose windowing functions: $w(t,t_m)$ with $t_m$ the center of the window.
2. Multiply windowing function with time series: $f_m(t) = f(t)w(t,t_m)$
3. Detrend the windowed signal.
4. Perform a DFT: $F_{km} = \Delta t\sum_{n=0}^N f_m(t)\exp(-2\pi i \frac{kn}{N})$
    and calculate the absolute value, $|F_{km}|$.
5. Plot the resulting matrix: $|F_{km}|$ in the time-frequency plane.

## Borehole Data and Test Site

Within the scope of constructing new buildings for the International Geothermal Center in Bochum in 2013 wells were drilled for the installation of a geothermal heat exchanger. Bore holes were drilled next to the newly constructed building (Station GEO3). A downhole hammer was used with a diameter of 152 mm. The drill bit operates by water flushing through the drill rod. The water flow rate determines the working frequency of the hammer.

To observe the drill bit noise a temporarily operating 2-D seismic network was installed around the drill site. Here, the noise of the used downhole hammer is investigated. An array of 16 seismological stations was installed in the test site. Four Mark L-4C-3D 1 Hz sensors, eight S-13 1 Hz sensors, one GS-13 1 Hz sensor and two Güralp CMG-3ESPC broad-band 120 sec – 50 Hz sensors were in use. Additionally an accelerometer was fixed to the drill rod (GEO11, blue triangle).

Some of the stations were positioned within one of the infrastructure tunnels servicing the university containing water conduits, long-distance heat line and electric cables (e.g. Station GEO4 and GEO05). Thus, noise could be reduced that might disturb the recordings. Other stations are located within buildings (e.g. Station GEO2 and GEO03) ore outside (e.g. Station GEO6 and GEO07).

![Map ot the stations at GZB](../images/karte3.jpg)

Drill bit noise was recorded up to the maximum drilling depth of 200 m. A drilling cycle is characterised by switching on the water pump, followed by the drilling with higher amplitude signals, that lasts several minutes. The water pump
is stopped about 5 to 15 minutes after the drilling finished depending on the drill depth.

In [ ]:
# Preparation: load packages
import os
from obspy.core import read
from obspy.core import UTCDateTime
import numpy as np
import matplotlib.pylab as plt

In [ ]:
# data from stations, Jan 23 2013

record = '1400'                                     # either use record starting at 1300 or 1400
station = 'GEO7'                                    # station code
#  available stations are GEO2, GEO3 (only 14:00), GEO4, GEO5, GEO6, GEO7

if record =='1300':
    stime = UTCDateTime('2013-01-23 13:16:00Z')      # use record starting at 1300
    etime = UTCDateTime('2013-01-23 13:25:00Z')
    ttitle = ', depth: 36.5 m'
else:
    stime = UTCDateTime('2013-01-23 14:17:00Z')      # use record starting at 1400 (14:14-14:23)
    etime = UTCDateTime('2013-01-23 14:19:00Z')
    ttitle = ', depth: 56.5 m'
    
datapath = "../data/{}/{}".format(station, 'e*'+record+'*.HHZ')      # search string for database
st = read(datapath)                                  # read file using obspy read
print(st)

st.trim(stime,etime)      # trim data stream to desired start and end time
st.detrend('linear')      # do a linear detrending
st.detrend('demean')      # subtract mean value
tr = st[0]                # extract first trace from stream (there is only one)
tr.plot();                 # plot trace

In [ ]:
# Cell 2: Preparation of window
wlen = 4.                                    # window length in seconds
npts = tr.stats.npts                         # number of samples
dt = tr.stats.delta                          # sampling interval

nwin = wlen/dt                                           # number of samples in window
nwin = int(pow(2, np.ceil(np.log(nwin)/np.log(2))))      # find next higher power of 2 of nwin
nwmax = int(pow(2, np.ceil(np.log(npts)/np.log(2))))/8   # maximum window length (about 1/8 of length)
nwin = min(nwin,nwmax)                                   # limit nwin
print("Samples in window: ",nwin)
print("Total number of samples: ",npts)
print("Sampling interval: ",dt)
print("Length of trace [s]: ",npts*dt)

In [ ]:
# The Hann window function
def hann(nw):
    arg = 2.*np.pi*np.arange(0,nw)/nw     # argument of cosine
    fwin = 0.5*(1.-np.cos(arg))           # Hann window
    return fwin

# The boxcar window function
def boxcar(nw):
    fwin = np.ones(nw)
    return fwin

In [ ]:
# Plot the window function and its effect on the time series
#
fwin = hann(nwin)           # Hann window
plt.figure(figsize = [15,6])
plt.subplot(221)
plt.plot(fwin,'-k')
plt.title("Hann window")
seg = tr.data[0:nwin]*fwin  # multiply data with window
plt.subplot(222)
plt.plot(seg,'-k')
fwin = boxcar(nwin)         # Boxcar window
plt.subplot(223)
plt.plot(fwin,'-k')
plt.title("Boxcar window")
seg = tr.data[0:nwin]*fwin  # multiply data with window
plt.subplot(224)
plt.plot(seg,'-k')
plt.show()

In [ ]:
def movingWindowAnalysis(data,winfun,nwin,shift):
    """
    Performs moving window analysis of a time series.
    data:   data array
    winfun: name of the window function to be called
    nwin:   number of window samples (power of 2)
    shift:  displacement of moving window in samples
    """
    fwin = winfun(nwin)                    # compute window values
    npts = len(data)                       # number of total samples
    nseg = int((npts-nwin)/shift)+1        # total number of expected data segment
    mwa = np.zeros((nwin//2+1,nseg))       # array for result (rfft returns N/2+1 samples)  
    wa = 0                                 # start index of data segment
    we = nwin                              # end index of data segment
    jseg = 0                               # initialize data segment counter
    while we < npts:                       # loop over segments
        seg = data[wa:we]*fwin                     # multiply data segment with window
        seg = seg-seg.mean()                       # subtract mean value of segment
        ftseg = np.abs(np.fft.rfft(seg))           # abs value of Fourier transform
        maxft = np.amax(ftseg)                     # max value of Fourier transform
        ftseg = ftseg/maxft+1.e-10                 # normalize spectrum to its maximum, remove zeros
        mwa[:,jseg] = np.power(ftseg,0.25)         # assign values to the matrix
        wa = wa+shift                              # move window start by shift
        we = we+shift                              # move window end by shift
        jseg = jseg+1                              # increase segment counter
    return nseg,mwa                         # return number of segments and moving window matrix

In [ ]:
# carry out the moving window analysis
tshift = 0.2*wlen
shift = int(tshift/dt)                                     # displacement of moving window in samples
nseg,mwa = movingWindowAnalysis(tr.data,hann,nwin,shift)   # compute spectrogram
freq = np.fft.rfftfreq(nwin,dt)                            # Fourier frequencies
print("Frequency range [Hz]: ",freq[0],freq[-1])

In [ ]:
# plot the result
fmaxplot = 250.                                            # maximum frequency to be plotted
nf = len(freq)                                             # number of frequencies
jfmax = int(fmaxplot/freq[-1]*nf)                          # max index for plotting   
extent = (0.5*wlen,0.5*wlen+nseg*tshift,fmaxplot,0.)       # extent of matrix in true time and frequency
plt.figure(figsize = [15,6])
plt.imshow(mwa[0:jfmax,:],extent = extent,aspect=0.25)      # do plotting
plt.xlabel('Window center time [s]')
plt.ylabel('Frequency [Hz]')
plt.show()

## Exercise 

1. Write a little routine for the Hamming window and do the analysis using this window
2. Use the sqrt of the Fourier amplitude spectrum as output and compare
3. Use other powers ($< 1$) of the Fourier amplitude (using np.power)
4. Use the logarithm of the Fourier amplitude as output and compare (using np.log)
5. Extend the frequency range when using the logarithm or a power of the Fourier amplitude
6. Do a moving window analysis for the other available stations. Which ones appear good and which ones are bad?
7. Try also records starting at 14:00

Hint: when you change something in the code, use "Run all below" to see the changes.

### The Hamming window
$ w(t) = 0.54 - 0.46 \cos \left( \frac{2 \pi t}{L} \right) ~ , t \in [0, L]$